In [ ]:
#Block 1
!sudo apt-get install git-lfs
!pip install huggingface_hub
!pip install --upgrade pip
!pip install -r requirements.txt
!huggingface-cli login

!pip install transformers[torch]
!pip install torch torchvision torchaudio
!pip install transformers -U
!pip install datasets -U
!pip install evaluate -U
!pip install accelerate -U

In [ ]:
#Block 2
import torch
import evaluate
from dataclasses import dataclass
from typing import Any, Dict, List, Union
from datasets import DatasetDict, Audio, load_from_disk, concatenate_datasets
from transformers.models.whisper.english_normalizer import BasicTextNormalizer
from transformers import WhisperFeatureExtractor, WhisperTokenizer, WhisperProcessor, WhisperForConditionalGeneration, Seq2SeqTrainingArguments, Seq2SeqTrainer

In [ ]:
#Block 3 do not run
import os
from datasets import load_dataset
import soundfile as sf

!pip install datasets soundfile

dataset = load_dataset("speechcolab/gigaspeech", "xs", split='train')
dataset = dataset.select(range(2))

audio_dir = "/content/gigaspeech_audio"
os.makedirs(audio_dir, exist_ok=True)

source_data_dir = "/content/source_data_directory"
os.makedirs(source_data_dir, exist_ok=True)

text_file_path = os.path.join(source_data_dir, "text_file.txt")
audio_paths_file_path = os.path.join(source_data_dir, "audio_paths_file.txt")

with open(text_file_path, "w") as text_file, open(audio_paths_file_path, "w") as audio_paths_file:
    for i, example in enumerate(dataset):
        unique_id = f"utt_{i}"

        audio_file_path = os.path.join(audio_dir, f"{unique_id}.wav")

        audio_data = example["audio"]["array"]
        sf.write(audio_file_path, audio_data, example["audio"]["sampling_rate"])

        text_file.write(f"{unique_id} {example['text']}\n")

        audio_paths_file.write(f"{unique_id} {audio_file_path}\n")

print("Files are prepared.")


In [ ]:
!pip install zipfile

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
import zipfile
import os

def extract_zip(zip_path, extract_to):
    """
    Extracts a zip file to a specified folder.

    Parameters:
    - zip_path: Path to the zip file.
    - extract_to: Destination folder path where contents will be extracted.
    """
    # Check if the zip file exists
    if not os.path.exists(zip_path):
        print(f"Zip file does not exist: {zip_path}")
        return

    # Check if the destination directory exists, if not create it
    if not os.path.exists(extract_to):
        os.makedirs(extract_to)

    # Extract the zip file
    with zipfile.ZipFile(zip_path, 'r') as zip_ref:
        zip_ref.extractall(extract_to)
        print(f"Extracted to {extract_to}")

# Example usage
#extract_zip('/content/drive/MyDrive/Projects/AudioFiles_final/voices_final.zip', '/content/temp_raw')
extract_zip('/content/drive/MyDrive/Projects/AudioFiles_final/voices_final_trimmed_2.zip', '/content/temp_raw')

In [ ]:
import os
import soundfile as sf
from scipy.signal import resample_poly
import numpy as np

def resample_wav_files(source_folder, destination_folder, target_sampling_rate=16000):

    if not os.path.exists(destination_folder):
        os.makedirs(destination_folder)


    for file_name in os.listdir(source_folder):
        if file_name.endswith('.wav'):
            source_path = os.path.join(source_folder, file_name)
            destination_path = os.path.join(destination_folder, file_name)


            data, sampling_rate = sf.read(source_path)


            resampling_rate = target_sampling_rate / sampling_rate


            if sampling_rate != target_sampling_rate:
                number_of_samples = round(len(data) * resampling_rate)
                data = resample_poly(data, target_sampling_rate, sampling_rate, axis=0)

            sf.write(destination_path, data, target_sampling_rate)
            print(f"Processed and saved: {destination_path}")

source_folder = '/content/temp_raw/male_voices'
destination_folder = '/content/gigaspeech_audio'
resample_wav_files(source_folder, destination_folder)

In [ ]:
import os
import soundfile as sf
from scipy.signal import resample_poly
import numpy as np

def resample_wav_files(source_folder, destination_folder, target_sampling_rate=16000):

    if not os.path.exists(destination_folder):
        os.makedirs(destination_folder)


    for file_name in os.listdir(source_folder):
        if file_name.endswith('.wav'):
            source_path = os.path.join(source_folder, file_name)
            destination_path = os.path.join(destination_folder, file_name)


            data, sampling_rate = sf.read(source_path)


            resampling_rate = target_sampling_rate / sampling_rate


            if sampling_rate != target_sampling_rate:
                number_of_samples = round(len(data) * resampling_rate)
                data = resample_poly(data, target_sampling_rate, sampling_rate, axis=0)

            sf.write(destination_path, data, target_sampling_rate)
            print(f"Processed and saved: {destination_path}")

source_folder = '/content/temp_raw/female_voices'
destination_folder = '/content/gigaspeech_audio'
resample_wav_files(source_folder, destination_folder)

In [ ]:
import os

# Path to your 'gigaspeech' folder
folder_path = '/content/gigaspeech_audio'

# List all files in the directory
file_list = [f for f in os.listdir(folder_path) if os.path.isfile(os.path.join(folder_path, f))]

# Count the number of files
number_of_files = len(file_list)

print(f"Number of files in the 'gigaspeech_audio' folder: {number_of_files}")

# Define the path to the directory containing the files
source_data_directory = '/content/source_data_directory'

# File names
audio_paths_file_name = 'audio_paths_file.txt'
text_file_name = 'text_file.txt'

# Function to count the number of rows in a file
def count_rows_in_file(file_path):
    with open(file_path, 'r') as file:
        return sum(1 for _ in file)

# Count rows in each file
audio_paths_file_rows = count_rows_in_file(os.path.join(source_data_directory, audio_paths_file_name))
text_file_rows = count_rows_in_file(os.path.join(source_data_directory, text_file_name))

# Print the results
print(f"Number of rows in '{audio_paths_file_name}': {audio_paths_file_rows}")
print(f"Number of rows in '{text_file_name}': {text_file_rows}")



In [ ]:
from datasets import Dataset, Audio, Value

source_data_dir = '/content/source_data_directory'
output_data_dir = '/content/output_data_directory'

os.makedirs(output_data_dir, exist_ok=True)

scp_entries = open(f"{source_data_dir}/audio_paths_file.txt", 'r').readlines()
txt_entries = open(f"{source_data_dir}/text_file.txt", 'r').readlines()

if len(scp_entries) == len(txt_entries):
    audio_dataset = Dataset.from_dict({
        "audio": [audio_path.split()[1].strip() for audio_path in scp_entries],
        "sentence": [' '.join(text_line.split()[1:]).strip() for text_line in txt_entries]
    })

    audio_dataset = audio_dataset.cast_column("audio", Audio(sampling_rate=16_000))
    audio_dataset = audio_dataset.cast_column("sentence", Value("string"))

    audio_dataset.save_to_disk(output_data_dir)
    print('Data preparation done.')
else:
    print('Please re-check the audio_paths and text files. They seem to have a mismatch in terms of the number of entries. Both these files should be carrying the same number of lines.')


In [ ]:
from datasets import load_from_disk, DatasetDict
import os


dataset_dir = '/content/output_data_directory'

full_dataset = load_from_disk(dataset_dir)


train_test_split = full_dataset.train_test_split(test_size=0.2)

split_dataset = DatasetDict({
    'train': train_test_split['train'],
    'eval': train_test_split['test']
})

train_dir = '/content/output_data_directory/train_dataset'
eval_dir = '/content/output_data_directory/eval_dataset'


os.makedirs(train_dir, exist_ok=True)
os.makedirs(eval_dir, exist_ok=True)


split_dataset['train'].save_to_disk(train_dir)
split_dataset['eval'].save_to_disk(eval_dir)

print("Train and eval datasets are saved.")

In [ ]:

import os
import logging
import string
from datasets import load_from_disk, DatasetDict, concatenate_datasets, Audio
from transformers import WhisperFeatureExtractor, WhisperTokenizer, WhisperProcessor, WhisperForConditionalGeneration

# Configure logging
logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)

# Define the Args class
class Args:
    model_name = 'openai/whisper-small'  # Model name
    language = 'English'  # Language
    sampling_rate = 16000
    num_proc = 8
    train_strategy = 'steps'  # Training strategy: 'steps' or 'epoch'
    learning_rate = 1.75e-5
    warmup = 2000
    train_batchsize = 48
    eval_batchsize = 32
    num_epochs = 20
    num_steps = 100
    resume_from_ckpt = None
    output_dir = '/content/output_model_directory'
    train_datasets = ['/content/output_data_directory/train_dataset']
    eval_datasets = ['/content/output_data_directory/eval_dataset']
    freeze_feature_encoder = False
    freeze_encoder = False
    gradient_checkpointing = True
    do_lower_case = False  # Lowercase the transcriptions if True
    do_remove_punctuation = False  # Remove punctuation from transcriptions if True

args = Args()

# Load the model and processor
model = WhisperForConditionalGeneration.from_pretrained(args.model_name)
processor = WhisperProcessor.from_pretrained(args.model_name, language=args.language, task="transcribe")

# Dataset Loading and Preparation Functions
def load_custom_dataset(split):
    ds = []
    if split == 'train':
        for dset in args.train_datasets:
            ds.append(load_from_disk(dset))
    elif split == 'eval':
        for dset in args.eval_datasets:
            ds.append(load_from_disk(dset))
    ds_to_return = concatenate_datasets(ds)
    ds_to_return = ds_to_return.shuffle(seed=22)
    return ds_to_return

def prepare_dataset(batch):
    audio = batch["audio"]
    batch["input_features"] = processor.feature_extractor(audio["array"], sampling_rate=audio["sampling_rate"]).input_features[0]
    batch["input_length"] = len(audio["array"]) / audio["sampling_rate"]
    transcription = batch["sentence"]
    if args.do_lower_case:
        transcription = transcription.lower()
    if args.do_remove_punctuation:
        transcription = transcription.translate(str.maketrans('', '', string.punctuation))
    batch["labels"] = processor.tokenizer(transcription, add_special_tokens=True).input_ids
    return batch

max_label_length = model.config.max_length
min_input_length = 0.0
max_input_length = 30.0

def is_in_length_range(length, labels):
    return min_input_length < length < max_input_length and 0 < len(labels) < max_label_length

# Load and prepare datasets
logger.info('DATASET PREPARATION IN PROGRESS...')
raw_dataset = DatasetDict()
raw_dataset["train"] = load_custom_dataset('train')
raw_dataset["eval"] = load_custom_dataset('eval')

raw_dataset = raw_dataset.cast_column("audio", Audio(sampling_rate=args.sampling_rate))
raw_dataset = raw_dataset.map(prepare_dataset, num_proc=args.num_proc)
raw_dataset = raw_dataset.filter(is_in_length_range, input_columns=["input_length", "labels"], num_proc=args.num_proc)

logger.info('DATASET PREPARATION COMPLETED')



In [ ]:
torch.set_num_threads(1)

In [ ]:
# Dataset Loading and Preparation Functions
def load_custom_dataset(split):
    ds = []
    if split == 'train':
        for dset in args.train_datasets:
            ds.append(load_from_disk(dset))
    elif split == 'eval':
        for dset in args.eval_datasets:
            ds.append(load_from_disk(dset))

    ds_to_return = concatenate_datasets(ds)
    ds_to_return = ds_to_return.shuffle(seed=22)
    return ds_to_return

def prepare_dataset(batch):
    audio = batch["audio"]
    batch["input_features"] = processor.feature_extractor(audio["array"], sampling_rate=audio["sampling_rate"]).input_features[0]
    batch["input_length"] = len(audio["array"]) / audio["sampling_rate"]
    transcription = batch["sentence"]
    if args.do_lower_case:
        transcription = transcription.lower()
    if args.do_remove_punctuation:
        transcription = normalizer(transcription).strip()
    batch["labels"] = processor.tokenizer(transcription).input_ids
    return batch

max_label_length = model.config.max_length
min_input_length = 0.0
max_input_length = 30.0
def is_in_length_range(length, labels):
    return min_input_length < length < max_input_length and 0 < len(labels) < max_label_length

# Load and prepare datasets
print('DATASET PREPARATION IN PROGRESS...')
raw_dataset = DatasetDict()
raw_dataset["train"] = load_custom_dataset('train')
raw_dataset["eval"] = load_custom_dataset('eval')

raw_dataset = raw_dataset.cast_column("audio", Audio(sampling_rate=args.sampling_rate))
raw_dataset = raw_dataset.map(prepare_dataset, num_proc=args.num_proc)
raw_dataset = raw_dataset.filter(is_in_length_range, input_columns=["input_length", "labels"], num_proc=args.num_proc)

print('DATASET PREPARATION COMPLETED')

In [ ]:
from transformers import WhisperFeatureExtractor, WhisperTokenizer, WhisperProcessor, WhisperForConditionalGeneration

# Assuming Args class and args are already defined as per the previous modification

feature_extractor = WhisperFeatureExtractor.from_pretrained(args.model_name)
tokenizer = WhisperTokenizer.from_pretrained(args.model_name, language=args.language, task="transcribe")
processor = WhisperProcessor.from_pretrained(args.model_name, language=args.language, task="transcribe")
model = WhisperForConditionalGeneration.from_pretrained(args.model_name)

if model.config.decoder_start_token_id is None:
    raise ValueError("Make sure that `config.decoder_start_token_id` is correctly defined")

if args.freeze_feature_encoder:
    model.freeze_feature_encoder()

if args.freeze_encoder:
    model.freeze_encoder()
    model.model.encoder.gradient_checkpointing = False

model.config.forced_decoder_ids = None
model.config.suppress_tokens = []

if args.gradient_checkpointing:
    model.config.use_cache = False

In [ ]:
import torch
from dataclasses import dataclass
from typing import Any, Dict, List, Union
import evaluate

!pip install jiwer

@dataclass
class DataCollatorSpeechSeq2SeqWithPadding:
    processor: Any

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        input_features = [{"input_features": feature["input_features"]} for feature in features]
        batch = self.processor.feature_extractor.pad(input_features, return_tensors="pt")

        label_features = [{"input_ids": feature["labels"]} for feature in features]
        labels_batch = self.processor.tokenizer.pad(label_features, return_tensors="pt")
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        if (labels[:, 0] == self.processor.tokenizer.bos_token_id).all().cpu().item():
            labels = labels[:, 1:]

        batch["labels"] = labels
        return batch

data_collator = DataCollatorSpeechSeq2SeqWithPadding(processor=processor)

# Load the metric
metric = evaluate.load("wer")

def compute_metrics(pred):
    pred_ids = pred.predictions
    label_ids = pred.label_ids

    label_ids[label_ids == -100] = processor.tokenizer.pad_token_id
    pred_str = processor.tokenizer.batch_decode(pred_ids, skip_special_tokens=True)
    label_str = processor.tokenizer.batch_decode(label_ids, skip_special_tokens=True)
    wer = 100 * metric.compute(predictions=pred_str, references=label_str)
    return {"wer": wer}

print('Data Collator and Metric Definition Completed')


In [ ]:
import torch
import gc

torch.cuda.empty_cache()
gc.collect()

import os

# Example: Set max_split_size_mb to 128 MB
os.environ['PYTORCH_CUDA_ALLOC_CONF'] = 'max_split_size_mb:128'

from transformers import Seq2SeqTrainingArguments, Seq2SeqTrainer
!pip install bitsandbytes

if args.train_strategy == 'epoch':
    training_args = Seq2SeqTrainingArguments(
        output_dir=args.output_dir,
        per_device_train_batch_size=args.train_batchsize,
        gradient_accumulation_steps=1,
        learning_rate=args.learning_rate,
        warmup_steps=args.warmup,
        gradient_checkpointing=args.gradient_checkpointing,
        fp16=True,
        evaluation_strategy="epoch",
        save_strategy="epoch",
        num_train_epochs=args.num_epochs,
        save_total_limit=10,
        per_device_eval_batch_size=args.eval_batchsize,
        predict_with_generate=True,
        generation_max_length=225,
        logging_steps=500,
        report_to=["tensorboard"],
        load_best_model_at_end=True,
        metric_for_best_model="wer",
        greater_is_better=False,
        optim="adamw_bnb_8bit",
        resume_from_checkpoint=args.resume_from_ckpt,
    )
elif args.train_strategy == 'steps':
        training_args = Seq2SeqTrainingArguments(
        output_dir=args.output_dir,
        per_device_train_batch_size=args.train_batchsize,
        gradient_accumulation_steps=1,
        learning_rate=args.learning_rate,
        warmup_steps=args.warmup,
        gradient_checkpointing=args.gradient_checkpointing,
        fp16=True,
        evaluation_strategy="steps",
        eval_steps=1000,
        save_strategy="steps",
        save_steps=1000,
        max_steps=args.num_steps,
        save_total_limit=10,
        per_device_eval_batch_size=args.eval_batchsize,
        predict_with_generate=True,
        generation_max_length=225,
        logging_steps=500,
        report_to=["tensorboard"],
        load_best_model_at_end=True,
        metric_for_best_model="wer",
        greater_is_better=False,
        optim="adamw_bnb_8bit",
        resume_from_checkpoint=args.resume_from_ckpt,
    )

trainer = Seq2SeqTrainer(
    model=model,
    args=training_args,
    train_dataset=raw_dataset["train"],
    eval_dataset=raw_dataset["eval"],
    data_collator=data_collator,
    compute_metrics=compute_metrics,
    tokenizer=processor.feature_extractor,
)

print('TRAINING IN PROGRESS...')
trainer.train()
print('DONE TRAINING')

model.save_pretrained(args.output_dir)
tokenizer.save_pretrained(args.output_dir)

In [ ]:
import shutil
import os

# Define the directory to be zipped and the destination directory
source_directory = '/content/output_model_directory'
destination_directory = '/content/drive/MyDrive/Projects'  # Adjust this to your specific location

# Define the path for the output zip file (without the .zip extension)
zip_file_path = '/content/drive/MyDrive/Projects/model_output_directory_small_zip'

# Create a zip file (including the path without the .zip extension)
shutil.make_archive(zip_file_path, 'zip', source_directory)

# Define the final path for the zip file in the destination directory (with the .zip extension)
final_zip_path = os.path.join(destination_directory, 'model_output_directory_small.zip')

# Move the zip file to the destination directory
shutil.move(f"{zip_file_path}.zip", final_zip_path)

print(f"Zip file created and moved to: {final_zip_path}")


In [ ]:
import os
from tqdm import tqdm
from transformers import pipeline
from datasets import Audio, load_from_disk
from transformers.models.whisper.english_normalizer import BasicTextNormalizer
import evaluate

wer_metric = evaluate.load("wer")
cer_metric = evaluate.load("cer")

whisper_norm = BasicTextNormalizer()


def is_target_text_in_range(sample):
    ref_text = get_text(sample)
    return ref_text.strip() != "" and ref_text.strip() != "ignore time segment in scoring"


def get_text(sample):
    if "text" in sample:
        return sample["text"]
    elif "sentence" in sample:
        return sample["sentence"]
    elif "normalized_text" in sample:
        return sample["normalized_text"]
    elif "transcript" in sample:
        return sample["transcript"]
    elif "transcription" in sample:
        return sample["transcription"]
    else:
        raise ValueError("Expected transcript column not found.")

def normalise(batch):
    batch["norm_text"] = whisper_norm(get_text(batch))
    return batch

def data(dataset):
    for item in dataset:
        # Ensure that 'array' is present in the audio dictionary
        if "array" in item["audio"]:
            yield {
                "raw": item["audio"]["array"],
                "sampling_rate": item["audio"]["sampling_rate"],
                "reference": get_text(item),
                "norm_reference": item["norm_text"]
            }
        else:
            # Handle cases where 'array' is not available
            raise ValueError("Audio data 'array' not found in the dataset item.")


hf_model = args.output_dir
language = "en"
eval_datasets = ['/content/output_data_directory/eval_dataset']
device = 0
batch_size = 16
output_dir = "predictions_dir"

os.makedirs(output_dir, exist_ok=True)


def main():

    hf_model ='/content/output_model_directory'
    tokenizer = WhisperTokenizer.from_pretrained(hf_model)

    whisper_asr = pipeline("automatic-speech-recognition", model=hf_model, tokenizer=tokenizer, device=device)


    for dset in eval_datasets:
        print('\nInfering on the dataset: ', dset)
        dataset = load_from_disk(dset)
        dataset = dataset.cast_column("audio", Audio(sampling_rate=16000))
        dataset = dataset.map(normalise, num_proc=1)
        dataset = dataset.filter(is_target_text_in_range, num_proc=1)

        predictions, references = [], []
        norm_predictions, norm_references = [], []


        for out in tqdm(whisper_asr(data(dataset), batch_size=batch_size), desc='Decode Progress'):
            predictions.append(out["text"])
            references.append(out["reference"][0])  # Unwrap the string from the list
            norm_predictions.append(whisper_norm(out["text"]))
            norm_references.append(out["norm_reference"][0])  # Unwrap the string from the list
            print("\nSample Predictions and References:")
            num_samples_to_display = 5  # You can adjust this number
            for i in range(min(num_samples_to_display, len(predictions))):
                print(f"\nSample {i+1}:")
                print("Prediction:", predictions[i])
                print("Reference:", references[i])
                print("Normalized Prediction:", norm_predictions[i])
                print("Normalized Reference:", norm_references[i])



        wer = wer_metric.compute(predictions=predictions, references=references)
        cer = cer_metric.compute(predictions=predictions, references=references)
        norm_wer = wer_metric.compute(predictions=norm_predictions, references=norm_references)
        norm_cer = cer_metric.compute(predictions=norm_predictions, references=norm_references)


        print(f"\nDataset: {dset}")
        print(f"WER: {wer*100:.2f}%, CER: {cer*100:.2f}%")
        print(f"Normalized WER: {norm_wer*100:.2f}%, Normalized CER: {norm_cer*100:.2f}%")


        results_filepath = os.path.join(output_dir, os.path.basename(dset) + '_results.txt')
        with open(results_filepath, 'w', encoding='utf-8') as file:
            file.write(f"Dataset: {dset}\n")
            file.write(f"WER: {wer*100:.2f}%, CER: {cer*100:.2f}%\n")
            file.write(f"Normalized WER: {norm_wer*100:.2f}%, Normalized CER: {norm_cer*100:.2f}%\n\n")
            for ref, pred in zip(references, predictions):
                file.write(f"Reference: {ref}\nPredicted: {pred}\n\n")
            print(f"Results saved to {output_dir}")

# Run the main function
main()


Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.



Infering on the dataset:  /content/output_data_directory/eval_dataset


Decode Progress: 4it [00:01,  3.71it/s]


Sample Predictions and References:

Sample 1:
Prediction:  I'm worried I might have Pheochromocytoma, I've been experiencing episodes of high blood pressure, severe headaches, and excessive sweating."
Reference: "I'm worried I might have Pheochromocytoma; I've been experiencing episodes of high blood pressure, severe headaches, and excessive sweating."
Normalized Prediction:  i m worried i might have pheochromocytoma i ve been experiencing episodes of high blood pressure severe headaches and excessive sweating 
Normalized Reference:  i m worried i might have pheochromocytoma i ve been experiencing episodes of high blood pressure severe headaches and excessive sweating 

Sample Predictions and References:

Sample 1:
Prediction:  I'm worried I might have Pheochromocytoma, I've been experiencing episodes of high blood pressure, severe headaches, and excessive sweating."
Reference: "I'm worried I might have Pheochromocytoma; I've been experiencing episodes of high blood pressure, severe h

Decode Progress: 10it [00:01,  9.74it/s]

...

Decode Progress: 1995it [04:01,  9.58it/s]


Sample Predictions and References:

Sample 1:
Prediction:  I'm worried I might have Pheochromocytoma, I've been experiencing episodes of high blood pressure, severe headaches, and excessive sweating."
Reference: "I'm worried I might have Pheochromocytoma; I've been experiencing episodes of high blood pressure, severe headaches, and excessive sweating."
Normalized Prediction:  i m worried i might have pheochromocytoma i ve been experiencing episodes of high blood pressure severe headaches and excessive sweating 
Normalized Reference:  i m worried i might have pheochromocytoma i ve been experiencing episodes of high blood pressure severe headaches and excessive sweating 

Sample 2:
Prediction:  I think I may have Cyclic Vomiting Syndrome because I've been noticing a pattern of sudden, uncontrollable vomiting episodes followed by symptom-free periods."
Reference: "I think I may have Cyclic Vomiting Syndrome because I've been noticing a pattern of sudden, uncontrollable vomiting episodes 

Decode Progress: 2000it [04:01,  8.28it/s]


Sample Predictions and References:

Sample 1:
Prediction:  I'm worried I might have Pheochromocytoma, I've been experiencing episodes of high blood pressure, severe headaches, and excessive sweating."
Reference: "I'm worried I might have Pheochromocytoma; I've been experiencing episodes of high blood pressure, severe headaches, and excessive sweating."
Normalized Prediction:  i m worried i might have pheochromocytoma i ve been experiencing episodes of high blood pressure severe headaches and excessive sweating 
Normalized Reference:  i m worried i might have pheochromocytoma i ve been experiencing episodes of high blood pressure severe headaches and excessive sweating 

Sample 2:
Prediction:  I think I may have Cyclic Vomiting Syndrome because I've been noticing a pattern of sudden, uncontrollable vomiting episodes followed by symptom-free periods."
Reference: "I think I may have Cyclic Vomiting Syndrome because I've been noticing a pattern of sudden, uncontrollable vomiting episodes 


Dataset: /content/output_data_directory/eval_dataset
WER: 12.62%, CER: 2.67%
Normalized WER: 3.03%, Normalized CER: 0.94%
Results saved to predictions_dir
